In [1]:
import folium
import matplotlib
from matplotlib.pyplot import imread
from matplotlib.colors import Normalize
from folium import raster_layers

In [2]:
image = '/notebooks/resources/gpm/gpm_1d.20190531.tif'

In [55]:
from osgeo import gdal,ogr,osr

def GetExtent(gt,cols,rows):
    ''' Return list of corner coordinates from a geotransform

        @type gt:   C{tuple/list}
        @param gt: geotransform
        @type cols:   C{int}
        @param cols: number of columns in the dataset
        @type rows:   C{int}
        @param rows: number of rows in the dataset
        @rtype:    C{[float,...,float]}
        @return:   coordinates of each corner
    '''
    ext=[]
    xarr=[0,cols]
    yarr=[0,rows]

    for px in xarr:
        for py in yarr:
            x=gt[0]+(px*gt[1])+(py*gt[2])
            y=gt[3]+(px*gt[4])+(py*gt[5])
            ext.append([x,y])
            print (x,y)
        yarr.reverse()
    return ext

def ReprojectCoords(coords,src_srs,tgt_srs):
    ''' Reproject a list of x,y coordinates.

        @type geom:     C{tuple/list}
        @param geom:    List of [[x,y],...[x,y]] coordinates
        @type src_srs:  C{osr.SpatialReference}
        @param src_srs: OSR SpatialReference object
        @type tgt_srs:  C{osr.SpatialReference}
        @param tgt_srs: OSR SpatialReference object
        @rtype:         C{tuple/list}
        @return:        List of transformed [[x,y],...[x,y]] coordinates
    '''
    trans_coords=[]
    transform = osr.CoordinateTransformation( src_srs, tgt_srs)
    for x,y in coords:
        x,y,z = transform.TransformPoint(x,y)
        trans_coords.append([x,y])
    return trans_coords

raster=image
ds=gdal.Open(raster)

gt=ds.GetGeoTransform()
cols = ds.RasterXSize
rows = ds.RasterYSize
ext=GetExtent(gt,cols,rows)

src_srs=osr.SpatialReference()
src_srs.ImportFromWkt(ds.GetProjection())
# tgt_srs=osr.SpatialReference()
# tgt_srs.ImportFromEPSG(4326)
tgt_srs = src_srs.CloneGeogCS()

geo_ext=ReprojectCoords(ext,src_srs,tgt_srs)

geo_fix = geo_ext
geo_fix[0] = geo_fix[0][::-1]
geo_fix[2] = geo_fix[2][::-1]
extent = geo_fix[2], geo_fix[0]
print(extent)


-180.0 10.0
-180.0 -60.0
-30.0 -60.0
-30.0 10.0
([-60.0, -30.0], [10.0, -180.0])


AttributeError: 'tuple' object has no attribute 'reverse'

In [56]:
m = folium.Map(
    control_scale=True 
)

data = matplotlib.pyplot.imread(image)

# Image bounds on the map in the form
# [[lat_min, lon_min], [lat_max, lon_max]]
m.add_child(raster_layers.ImageOverlay(
      data
#     , bounds = [[-60.0000000000000000, -30.0000000000000000], [10.0000000000000000, -180.0000000000000000]]
    , bounds = extent
    , mercator_project = True
)
           )

In [ ]:
print(data)
print(data.shape)
# data = data.transpose()
# print(data)
# print(data.shape)

In [ ]:
!gdalinfo '/notebooks/resources/gpm/gpm_1d.20190531.tif'

In [ ]:
# First: read the geotiff image with GDAL.
from osgeo import gdal, osr

gdal.UseExceptions()

ds = gdal.Open(image)
data = ds.ReadAsArray()
gt = ds.GetGeoTransform()
proj = ds.GetProjection()

inproj = osr.SpatialReference()
inproj.ImportFromWkt(proj)

print('\n\n## ds ##:\n\n' + str(ds))
print('\n\n## data ##:\n\n' + str(data))
print('\n\n## gt ##:\n\n' + str(gt))
print('\n\n## proj ##:\n\n' + str(proj))
print('\n\n## inproj ##:\n\n' + str(inproj))